In [5]:
# IMPORTANT always restart from here!
import pandas as pd 
import numpy as np
import altair as alt

# parameters

# wvs.csv has 440056 wvs.csv lines
# currently, 80k is the maximum we can reliably handle on 12gb RAM
WVS_MAX_ROWS=80000 

In [6]:
# I. Prepare cpi.csv

cpi = pd.read_csv('../0_datasets/cpi.csv', sep=',', na_values=['-'])
cpi.head()

Jurisdiction  1998  1999  2000  2001  2002  2003  2004  2005  2006  2007  \
0  Afghanistan   NaN   NaN   NaN   NaN   NaN   NaN   NaN   2.5   NaN   1.8   
1      Albania   NaN   2.3   NaN   NaN   2.5   2.5   2.5   2.4   2.6   2.9   
2      Algeria   NaN   NaN   NaN   NaN   NaN   2.6   2.7   2.8   3.1   3.0   
3       Angola   NaN   NaN   1.7   NaN   1.7   1.8   2.0   2.0   2.2   2.2   
4    Argentina   3.0   3.0   3.5   3.5   2.8   2.5   2.5   2.8   2.9   2.9   

   2008  2009  2010  2011  2012  2013  2014  2015  
0   1.5   1.3   1.4  1.52   8.0   8.0  12.0  11.0  
1   3.4   3.2   3.3  3.05  33.0  31.0  33.0  36.0  
2   3.2   2.8   2.9  2.90  34.0  36.0  36.0  36.0  
3   1.9   1.9   1.9  2.01  22.0  23.0  19.0  15.0  
4   2.9   2.9   2.9  3.00  35.0  34.0  34.0  32.0

In [7]:
# A) Normalize values
# From 2012 onwards, the methology changed (scala went from 0-10 to 0-100)
years100 = ['2012', '2013', '2014', '2015']
cpi[years100] = cpi[years100].applymap(lambda v: v / 100.0)

# B) Long Format
# Long format is more desireable, as we want to join it with WVS later on
cpi = cpi.melt(id_vars=['Jurisdiction'], var_name='Year', value_name='CPI-Value')
cpi.head()

Jurisdiction  Year  CPI-Value
0  Afghanistan  1998        NaN
1      Albania  1998        NaN
2      Algeria  1998        NaN
3       Angola  1998        NaN
4    Argentina  1998        3.0

In [8]:
# II Prepare wvs_variables.csv

wvs_vars = pd.read_csv('../0_datasets/wvs-variables.csv')
wvs_vars.head()

Variable                            Title WVS7 WVS6 WVS5 WVS4 WVS3 WVS2 WVS1
0     A001        Important in life: Family   Q1   V4   V4   V4   V4   V5  NaN
1     A002       Important in life: Friends   Q2   V5   V5   V5   V5   V6  NaN
2     A003  Important in life: Leisure time   Q3   V6   V6   V6   V6   V7  NaN
3     A004      Important in life: Politics   Q4   V7   V7   V7   V7   V8  NaN
4     A005          Important in life: Work   Q5   V8   V8   V8   V8   V4  NaN

In [9]:
# A) Remove unwanted prefixes 
# We want to use the Title as human-readable labels later on
wvs_vars['Title'].replace(r'[^ ]+-\ ', '', regex=True, inplace=True)

# B) Drop unneeded internal variables
wvs_vars = wvs_vars.drop(wvs_vars.loc[:, 'WVS7':'WVS1'], axis=1)

# C) Set the variable name as key
wvs_vars.set_index('Variable', inplace=True)
wvs_vars.head()

Title
Variable                                 
A001            Important in life: Family
A002           Important in life: Friends
A003      Important in life: Leisure time
A004          Important in life: Politics
A005              Important in life: Work

In [10]:
# III Prepare wvs.csv

wvs = pd.read_csv('../0_datasets/wvs.csv', sep=';', nrows=WVS_MAX_ROWS, na_values=['', ' '])
wvs.head()

version                        doi  S002VS  S003 COUNTRY_ALPHA  \
0  3-0-0 (2022-03-14)  doi.org/10.14281/18241.17       3     8           ALB   
1  3-0-0 (2022-03-14)  doi.org/10.14281/18241.17       3     8           ALB   
2  3-0-0 (2022-03-14)  doi.org/10.14281/18241.17       3     8           ALB   
3  3-0-0 (2022-03-14)  doi.org/10.14281/18241.17       3     8           ALB   
4  3-0-0 (2022-03-14)  doi.org/10.14281/18241.17       3     8           ALB   

   COW_NUM COW_ALPHA  S006      S007  S008  ...  Y021C  Y022A  Y022B  Y022C  \
0      339       ALB     1  80320001    -4  ...    0.0    0.0   0.66   1.00   
1      339       ALB     2  80320002    -4  ...    0.0    0.0   0.00   1.00   
2      339       ALB     3  80320003    -4  ...    0.0    0.0   1.00   1.00   
3      339       ALB     4  80320004    -4  ...    0.0    0.0   0.00   0.66   
4      339       ALB     5  80320005    -4  ...    0.0    0.0   0.00   0.66   

      Y023A     Y023B     Y023C  Y024A  Y024B  Y024C  
0  0.000000  0.444444  0.444444   0.33    0.0  0.165  
1  0.111111  0.444444  0.444444   0.33    0.0  0.165  
2  0.000000  0.444444  0.444444   0.33    0.5  0.415  
3  0.000000  0.333333  0.333333   0.33    0.0  0.165  
4  0.000000  0.333333  0.333333   0.00    0.5  0.250  

[5 rows x 1041 columns]

In [11]:
# A) Remove unused meta variables, only keep CountryCode and Year
wvs_countryYear = pd.DataFrame({'Country': wvs['S003'], 'Year': wvs['S020']})
wvs.drop(wvs.loc[:, :'S025'], axis = 1, inplace=True)
wvs.head()

A001  A002  A003  A004  A005  A006  A008  A009  A010  A011  ...  Y021C  \
0     1     2     2     4     2     2     3     1    -4    -4  ...    0.0   
1     1     2     2     3     2     2     2     1    -4    -4  ...    0.0   
2     1     2     2     4     1     1     3     2    -4    -4  ...    0.0   
3     1     2     2     3     2     2     3     3    -4    -4  ...    0.0   
4     1     2     2     4     1     1     3     2    -4    -4  ...    0.0   

   Y022A  Y022B  Y022C     Y023A     Y023B     Y023C  Y024A  Y024B  Y024C  
0    0.0   0.66   1.00  0.000000  0.444444  0.444444   0.33    0.0  0.165  
1    0.0   0.00   1.00  0.111111  0.444444  0.444444   0.33    0.0  0.165  
2    0.0   1.00   1.00  0.000000  0.444444  0.444444   0.33    0.5  0.415  
3    0.0   0.00   0.66  0.000000  0.333333  0.333333   0.33    0.0  0.165  
4    0.0   0.00   0.66  0.000000  0.333333  0.333333   0.00    0.5  0.250  

[5 rows x 1014 columns]

In [12]:
# B) normalize all values
# * we have some suspicious values (-4), replace them with NaN
# * we have column with different ranges ([0.0, 1.0], [0.0, 10.0], we normalize them to [0, 1.0]
#wvs = wvs.astype(np.float64)

#wvs_minMax = pd.DataFrame(columns=wvs.columns, index=['min','max'], data=[wvs.min(axis=0).values, wvs.max(axis=0).values])
#wvs_minMax.head()
#wvs.min(axis = 0).concat(wvs.max(axis = 0))

In [13]:
# C) we replace variable codes with variable titles
wvs.rename(columns=wvs_vars['Title'], inplace=True)

# D) re-insert CountryCode and Year column
wvs.insert(0, 'Year', wvs_countryYear['Year'])
wvs.insert(1, 'Country', wvs_countryYear['Country'])
wvs.set_index(['Year', 'Country'])

# E) convert from wide into long format
wvs = wvs.melt(id_vars=['Year', 'Country'], var_name='Variable', value_name='Value')

wvs.head()

Year  Country                   Variable  Value
0  1998        8  Important in life: Family    1.0
1  1998        8  Important in life: Family    1.0
2  1998        8  Important in life: Family    1.0
3  1998        8  Important in life: Family    1.0
4  1998        8  Important in life: Family    1.0

In [14]:
wvsSummary = wvs.groupby(['Year', 'Country', 'Variable']).mean().reset_index()
wvs = None # free memory
wvsSummary.head()

Year  Country                                           Variable     Value
0  1981       36  A truly Islamic country should not have a parl... -4.000000
1  1981       36       A woman has to have children to be fulfilled -1.062704
2  1981       36  AUTHORITY - Welzel defiance - 1: Inverse respe...  0.195242
3  1981       36              Abortion if not wanting more children -4.000000
4  1981       36         Abortion when child physically handicapped -4.000000

In [15]:
# IV Prepare country-codes.csv
countryCodes = pd.read_csv('../0_datasets/country-codes.csv')
countryCodes.head()

name alpha-2 alpha-3  country-code     iso_3166-2   region  \
0     Afghanistan      AF     AFG             4  ISO 3166-2:AF     Asia   
1   Åland Islands      AX     ALA           248  ISO 3166-2:AX   Europe   
2         Albania      AL     ALB             8  ISO 3166-2:AL   Europe   
3         Algeria      DZ     DZA            12  ISO 3166-2:DZ   Africa   
4  American Samoa      AS     ASM            16  ISO 3166-2:AS  Oceania   

        sub-region intermediate-region  region-code  sub-region-code  \
0    Southern Asia                 NaN        142.0             34.0   
1  Northern Europe                 NaN        150.0            154.0   
2  Southern Europe                 NaN        150.0             39.0   
3  Northern Africa                 NaN          2.0             15.0   
4        Polynesia                 NaN          9.0             61.0   

   intermediate-region-code  
0                       NaN  
1                       NaN  
2                       NaN  
3                       NaN  
4                       NaN

In [16]:
countryCodes = countryCodes[['name', 'country-code']].set_index('country-code')
countryCodes.head()

name
country-code                
4                Afghanistan
248            Åland Islands
8                    Albania
12                   Algeria
16            American Samoa

In [17]:
wvsSummaryCC = wvsSummary.copy()
wvsSummaryCC['Country'] = countryCodes.loc[wvsSummary['Country']]['name'].values
wvsSummaryCC.rename(columns={"Variable": "VariableTitle", "Country": "CountryName"}, inplace=True)
wvsSummaryCC.head()

Year CountryName                                      VariableTitle  \
0  1981   Australia  A truly Islamic country should not have a parl...   
1  1981   Australia       A woman has to have children to be fulfilled   
2  1981   Australia  AUTHORITY - Welzel defiance - 1: Inverse respe...   
3  1981   Australia              Abortion if not wanting more children   
4  1981   Australia         Abortion when child physically handicapped   

      Value  
0 -4.000000  
1 -1.062704  
2  0.195242  
3 -4.000000  
4 -4.000000

In [18]:
varTitles = pd.Series(wvsSummaryCC['VariableTitle'].unique())
importantInLife = varTitles[varTitles.str.contains('Important in life')].tolist()
importantInLife

['Important in life: Family',
 'Important in life: Friends',
 'Important in life: Leisure time',
 'Important in life: Politics',
 'Important in life: Religion',
 'Important in life: Work']

In [19]:
alt.data_transformers.enable('default', max_rows=None)

nearest = alt.selection(type='single', nearest=True, on='mouseover',
                            fields=['CountryName', 'Value', 'VariableTitle', 'Year'])

alt.Chart(wvsSummaryCC).mark_line().encode(
    alt.X('Year:O'),
    alt.Y('Value:Q'),
    alt.Color('CountryName:N'),
    #alt.Color('CountryName:N'),
    alt.Tooltip(['CountryName', 'Value', 'VariableTitle', 'Year'])
).transform_filter(
    alt.FieldOneOfPredicate(field='VariableTitle', oneOf=importantInLife)
).transform_filter(
    alt.FieldRangePredicate(field='Year', range=[1995, 2010])
).facet(
    column='VariableTitle:N'
).add_selection(
    nearest
)

# TODO nicer tooltips:
# https://stackoverflow.com/questions/53287928/tooltips-in-altair-line-charts

alt.FacetChart(...)

In [20]:
wvsCountries = wvsSummaryCC['CountryName'].unique()
wvsCountries

array(['Australia', 'Canada', 'Argentina', 'Belarus', 'Brazil',
       'Bangladesh', 'Croatia', 'Azerbaijan', 'Armenia', 'Bulgaria',
       'Colombia', 'Albania', 'Bosnia and Herzegovina', 'Algeria',
       'Andorra', 'Cyprus', 'Burkina Faso',
       'Bolivia (Plurinational State of)'], dtype=object)